## Python Code for scraping Syuuin speech
#### Data Management (Spring/Summer 2018) at OSIPP, Osaka U

#### Notes: Make sure to use API if you download many many texts. [Link](http://kokkai.ndl.go.jp/api.html)

### Preamble

In [2]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import numpy as np
import pandas as pd
import time as t

In [3]:
path_to_chromedriver = "C:\\Users\\shu\\Desktop\\chromedriver" # set path to your chrome driver
browser = webdriver.Chrome(executable_path = path_to_chromedriver) # launch Google Chrome

browser.implicitly_wait(10) # wait 10 sec

### Find relevant data

In [4]:
url = 'http://kokkai.ndl.go.jp/' 
browser.get(url) # open the webpage

In [5]:
browser.find_element_by_id('b_easy-search').click() # click 'easy search'

In [6]:
browser.switch_to_frame("frame1") # select the first frame (there are two frames)

#### - Start and end date
- I choose the period between 2017/4/1 and 2018/3/31.

In [7]:
fromY = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[3]/input[2]'
fromM = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[3]/input[3]'
fromD = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[3]/input[4]'

browser.find_element_by_xpath(fromY).clear() # use xpath to select "fromY" as defined above
browser.find_element_by_xpath(fromY).send_keys('29')  # start year
browser.find_element_by_xpath(fromM).clear()
browser.find_element_by_xpath(fromM).send_keys('4')  # start month
browser.find_element_by_xpath(fromD).clear()
browser.find_element_by_xpath(fromD).send_keys('1')  # start date

In [8]:
toY = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[2]/td/input[1]'
toM = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[2]/td/input[2]'
toD = '/html/body/table[4]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[2]/td/input[3]'

browser.find_element_by_xpath(toY).clear()
browser.find_element_by_xpath(toY).send_keys('30')  # end year
browser.find_element_by_xpath(toM).clear()
browser.find_element_by_xpath(toM).send_keys('3')  # end month
browser.find_element_by_xpath(toD).clear()
browser.find_element_by_xpath(toD).send_keys('31')  # end date

#### - Meetings
- Select the House of Representatives (Syuuin).

In [9]:
all_meetings = '/html/body/p[2]/table/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[2]/table/tbody/tr/td[1]/input'
syuuin       = '/html/body/p[2]/table/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[2]/table/tbody/tr/td[3]/input'
sannin       = '/html/body/p[2]/table/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[2]/table/tbody/tr/td[5]/input'
ryouin       = '/html/body/p[2]/table/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[1]/td[2]/table/tbody/tr/td[7]/input'

browser.find_element_by_xpath(syuuin).click() # you can change syuuin to another option

#### - Keywords
- Use "TPP" as a keyword.

In [10]:
clue = '/html/body/p[3]/table[1]/tbody/tr[2]/td[2]/table/tbody/tr/td/table/tbody/tr[2]/td/input'

browser.find_element_by_xpath(clue).send_keys('TPP')

#### - Click 'Search'

In [11]:
t.sleep(3) 

browser.find_element_by_xpath('/html/body/p[3]/table[2]/tbody/tr/td/table/tbody/tr/td[1]/a/img').click()

#### - Show results in the browser

In [12]:
t.sleep(3)

browser.find_element_by_xpath('/html/body/table[4]/tbody/tr/td[6]/a/img').click()

### Get attributes
- We will scrape attributes shown only on the first page (20 rows). If you want to scrape all results, you need to make a loop to go through the rest of the pages.
- Attributes include: (a) the session number, (b) the name of a house, (c) the name of a meeting, (d) the number of the meeting, and (e) the date of the meeting

In [13]:
attr = browser.find_elements_by_xpath('/html/body/table[7]/tbody/tr/td[2]/table/tbody/tr/td')

## create a list and put texts. results include 180 rows in this case.
attr_list = [] 
for i in range(0,180):
    attr_list.append(attr[i].text)

## convert the list to a 20 * 9 matrix (Numpy array), then to a data frame
df_attr = pd.DataFrame(np.reshape(attr_list, (20, 9))) 
df_attr = df_attr.iloc[:,1:6] # drop empty columns
df_attr

1    2              3    4            5
0   196  衆議院        財務金融委員会  10号  平成30年03月30日
1   196  衆議院        経済産業委員会   3号  平成30年03月30日
2   196  衆議院        農林水産委員会   5号  平成30年03月28日
3   196  衆議院          内閣委員会   5号  平成30年03月28日
4   196  衆議院        厚生労働委員会   5号  平成30年03月28日
5   196  衆議院        経済産業委員会   2号  平成30年03月28日
6   196  衆議院        経済産業委員会   1号  平成30年03月23日
7   196  衆議院          外務委員会   4号  平成30年03月23日
8   196  衆議院  地方創生に関する特別委員会   6号  平成30年03月22日
9   196  衆議院        農林水産委員会   3号  平成30年03月20日
10  196  衆議院        財務金融委員会   8号  平成30年03月20日
11  196  衆議院        農林水産委員会   2号  平成30年03月15日
12  196  衆議院          外務委員会   2号  平成30年03月09日
13  196  衆議院        農林水産委員会   1号  平成30年03月06日
14  196  衆議院        国土交通委員会   2号  平成30年03月06日
15  196  衆議院          内閣委員会   1号  平成30年03月02日
16  196  衆議院          外務委員会   1号  平成30年03月02日
17  196  衆議院     予算委員会第六分科会   2号  平成30年02月26日
18  196  衆議院     予算委員会第七分科会   1号  平成30年02月23日
19  196  衆議院          予算委員会   9号  平成30年02月09日

### Open each meeting page and get texts

In [14]:
text_list = []  # make an empty list
j = 1
for i in range(2,22):
    browser.find_element_by_xpath('/html/body/table[7]/tbody/tr/td[2]/table/tbody/tr['+str(i)+']/td[9]/a').click() # click a meeting
    browser.switch_to.window(browser.window_handles[j]) # switch to a new tab
    browser.switch_to_frame("MAIN1") # select the main frame
    text_list.append(browser.find_element_by_xpath('/html/body').text) # get the element
    browser.switch_to.window(browser.window_handles[0]) # switch back to the original tab
    j += 1
    t.sleep(2) # wait for 2 sec
len(text_list)
text_list

['第１９６回国会\u3000財務金融委員会\u3000第１０号\n平成三十年三月三十日（金曜日）\n午後四時五分開議\n出席委員\n委員長\u3000小里\u3000泰弘君\n理事\u3000あべ\u3000俊子君\u3000理事\u3000井林\u3000辰憲君\n理事\u3000津島\u3000\u3000淳君\u3000理事\u3000三ッ矢憲生君\n理事\u3000義家\u3000弘介君\u3000理事\u3000海江田万里君\n理事\u3000岸本\u3000周平君\u3000理事\u3000斉藤\u3000鉄夫君\n石崎\u3000\u3000徹君\u3000\u3000\u3000\u3000今枝宗一郎君\n勝俣\u3000孝明君\u3000\u3000\u3000\u3000神田\u3000憲次君\n小泉\u3000龍司君\u3000\u3000\u3000\u3000國場幸之助君\n斎藤\u3000洋明君\u3000\u3000\u3000\u3000柴山\u3000昌彦君\n鈴木\u3000隼人君\u3000\u3000\u3000\u3000田畑\u3000\u3000毅君\n武井\u3000俊輔君\u3000\u3000\u3000\u3000中山\u3000展宏君\n藤丸\u3000\u3000敏君\u3000\u3000\u3000\u3000本田\u3000太郎君\n牧島かれん君\u3000\u3000\u3000\u3000御法川信英君\n宗清\u3000皇一君\u3000\u3000\u3000\u3000山田\u3000賢司君\n山田\u3000美樹君\u3000\u3000\u3000\u3000川内\u3000博史君\n末松\u3000義規君\u3000\u3000\u3000\u3000高木錬太郎君\n青山\u3000大人君\u3000\u3000\u3000\u3000今井\u3000雅人君\n近藤\u3000和也君\u3000\u3000\u3000\u3000遠山\u3000清彦君\n野田\u3000佳彦君\u3000\u3000\u3000\u3000宮本\u3000\u3000徹君\n杉本\u3000和巳君\u3000\u3000\u3000\u3000青山\u3000雅幸君\n鷲尾英一郎君\n………………………

In [15]:
df_text = pd.DataFrame(text_list) # convert the list to a data frame
df_text.shape # check the shape of df_text
df_text.iloc[0,0] # check the first row

'第１９６回国会\u3000財務金融委員会\u3000第１０号\n平成三十年三月三十日（金曜日）\n午後四時五分開議\n出席委員\n委員長\u3000小里\u3000泰弘君\n理事\u3000あべ\u3000俊子君\u3000理事\u3000井林\u3000辰憲君\n理事\u3000津島\u3000\u3000淳君\u3000理事\u3000三ッ矢憲生君\n理事\u3000義家\u3000弘介君\u3000理事\u3000海江田万里君\n理事\u3000岸本\u3000周平君\u3000理事\u3000斉藤\u3000鉄夫君\n石崎\u3000\u3000徹君\u3000\u3000\u3000\u3000今枝宗一郎君\n勝俣\u3000孝明君\u3000\u3000\u3000\u3000神田\u3000憲次君\n小泉\u3000龍司君\u3000\u3000\u3000\u3000國場幸之助君\n斎藤\u3000洋明君\u3000\u3000\u3000\u3000柴山\u3000昌彦君\n鈴木\u3000隼人君\u3000\u3000\u3000\u3000田畑\u3000\u3000毅君\n武井\u3000俊輔君\u3000\u3000\u3000\u3000中山\u3000展宏君\n藤丸\u3000\u3000敏君\u3000\u3000\u3000\u3000本田\u3000太郎君\n牧島かれん君\u3000\u3000\u3000\u3000御法川信英君\n宗清\u3000皇一君\u3000\u3000\u3000\u3000山田\u3000賢司君\n山田\u3000美樹君\u3000\u3000\u3000\u3000川内\u3000博史君\n末松\u3000義規君\u3000\u3000\u3000\u3000高木錬太郎君\n青山\u3000大人君\u3000\u3000\u3000\u3000今井\u3000雅人君\n近藤\u3000和也君\u3000\u3000\u3000\u3000遠山\u3000清彦君\n野田\u3000佳彦君\u3000\u3000\u3000\u3000宮本\u3000\u3000徹君\n杉本\u3000和巳君\u3000\u3000\u3000\u3000青山\u3000雅幸君\n鷲尾英一郎君\n…………………………

### Merge attributes with texts
- We have scraped attributes and texts. Let's merge them!

In [16]:
data = df_attr.join(df_text) # join texts to attributes
data.columns = ['kai','house','m_name','gou','date','content'] # add column names
data.shape # check the shape

dta = [elem.strip().replace('\n','') for elem in data.content] # remove \n
lst = [elem.strip().split('○') for elem in dta] # split per speaker

## select speaches including 安倍
abe_list = []
for i in range(0,len(lst)):
    abe_list.append([x for x in lst[i] if "安倍" in x]) 

abe_col = ['s' + str(x) for x in range(0,20)] # make column names
abe_list = pd.DataFrame(abe_list,columns=abe_col) # convert the list to a data frame
abe_list

del(data['content']) # drop content variable

data = pd.merge(data, abe_list,right_index=True,left_index=True) # merge abe_list
data

kai house         m_name  gou         date  \
0   196   衆議院        財務金融委員会  10号  平成30年03月30日   
1   196   衆議院        経済産業委員会   3号  平成30年03月30日   
2   196   衆議院        農林水産委員会   5号  平成30年03月28日   
3   196   衆議院          内閣委員会   5号  平成30年03月28日   
4   196   衆議院        厚生労働委員会   5号  平成30年03月28日   
5   196   衆議院        経済産業委員会   2号  平成30年03月28日   
6   196   衆議院        経済産業委員会   1号  平成30年03月23日   
7   196   衆議院          外務委員会   4号  平成30年03月23日   
8   196   衆議院  地方創生に関する特別委員会   6号  平成30年03月22日   
9   196   衆議院        農林水産委員会   3号  平成30年03月20日   
10  196   衆議院        財務金融委員会   8号  平成30年03月20日   
11  196   衆議院        農林水産委員会   2号  平成30年03月15日   
12  196   衆議院          外務委員会   2号  平成30年03月09日   
13  196   衆議院        農林水産委員会   1号  平成30年03月06日   
14  196   衆議院        国土交通委員会   2号  平成30年03月06日   
15  196   衆議院          内閣委員会   1号  平成30年03月02日   
16  196   衆議院          外務委員会   1号  平成30年03月02日   
17  196   衆議院     予算委員会第六分科会   2号  平成30年02月26日   
18  196   衆議院     予算委員会第七分科会   1号  平成30年02月23日   
19  196   衆議院          予算委員会   9号  平成30年02月09日   

                                                   s0  \
0   川内委員　川内でございます。よろしくお願いをいたします。まず、麻生大臣に聞かせていただきたい...   
1   斉木委員　日銀の組織目標である物価安定、そしてそれを二％の物価上昇率を達成するまで続けるとい...   
2   佐々木（隆）委員　先ほどの所得倍増もそうなんですが、いわゆる先ほどの所得倍増のところでは、総...   
3   阿部委員　立憲民主党の阿部知子です。本委員会の冒頭で山際委員長から御発言がありましたように、...   
4   池田（真）委員　はい。昨年末から大きな動きがあったということで、厚労委員会ですから、厚生労働...   
5   辻委員　このタイミングで、事業承継もそうですけれども、スムーズな経営者移転ができなければ、潰...   
6                                                None   
7   篠原（豪）委員　それは、現状を見れば、たまたま雇われている全員が軍属であったということにすぎ...   
8   篠原（孝）委員　無所属の会の篠原でございます。質問の順番、一番、二番は時間があったらやらせて...   
9   神谷（裕）委員　まさしく、資源管理、本当に重要な話でございます。今、ＡＢＣの話であるとか、あ...   
10  末松委員　私も森友問題は初めてなんですけれども、この森友問題を俯瞰すると、多数の報道に出てい...   
11                                               None   
12  遠山委員　大臣、ありがとうございます。私も、大臣の考えと全く一緒でございます。北朝鮮の最近の...   
13  齋藤国務大臣　農林水産委員会の開催に当たりまして、農林水産行政に関する基本的な考え方について...   
14                                               None   
15  菅国務大臣　初めに、北朝鮮の核・ミサイル開発について申し上げます。北朝鮮の核・ミサイル開発は...   
16                                               None   
17  国光分科員　ありがとうございます。一歩一歩着実に進んでいらっしゃるという御様子はよく承知をい...   
18  岡下分科員　ありがとうございます。実は、私も、今大臣も胸につけていただいているバッジ、これは...   
19  茂木国務大臣　安倍政権では、これまで、委員御指摘の経済・財政再生計画に基づきまして、複数年度...   

                                                   s1  \
0   川内委員　最終的な段階って、問題が全部終わっちゃったら終わっちゃうわけで、結局改ざんでしたと...   
1   斉木委員　そのためには、私は、二％に達するまでマイナス金利に拘泥するような、目的と手段が逆に...   
2                                                None   
3   山崎委員　今の御説明で、今回明らかとなったような改ざん事案というのは発生していないと。制度上...   
4   高橋（千）委員　日本共産党の高橋千鶴子です。初めに、先月二十日に、米軍三沢基地所属のＦ16戦...   
5   落合委員　これは責任を持ってしっかり取り組んでいただければと思います。たしか五月あたりに、プ...   
6                                                None   
7   篠原（豪）委員　補足協定として、日米合同委員会が発表した合意には、軍属として八種別を挙げてい...   
8   宮本（岳）委員　私は、日本共産党を代表して、地域における大学の振興及び若者の雇用機会の創出に...   
9   後藤（祐）委員　この再交渉の話については、予算委員会でも確認させていただきました。将来におけ...   
10  末松委員　なぜこういうふうに私が言うかというと、この決めたことに対して、後、佐川前局長も、今...   
11                                               None   
12  遠山委員　ありがとうございます。ちょっと時間の関係で、経済産業省は、済みません、割愛をさせて...   
13                                               None   
14                                               None   
15  松山国務大臣　一億総活躍担当大臣、また、少子化対策、クールジャパン戦略を担当する内閣府特命担...   
16                                               None   
17                                               None   
18  岡田分科員　規制委員会の方は、最低限クリアすべきそういうラインを引いて、それをクリアしている...   
19  武内委員　局長始め役所の皆さんに、行政機関のところに、再度しっかりと要請をさせてもらいたいと...   

                                                   s2  \
0   川内委員　内閣官房の方にきょう来ていただいておりますので、教えていただきたいんですけれども、...   
1   世耕国務大臣　私は全くそういうことは意識をせずに、安倍内閣というのは、仕事をしっかりやって成...   
2                                                None   
3   吉良委員　ＴＰＰの意義についてと今後について私の方からお伺いしましたけれども、私自身は、この...   
4   柚木委員　これは、この間も、参議院も含めて、予算委員会の中で、衆議院も含めて、例えば三月の五...   
5   中谷（一）委員　立憲民主党の中谷一馬でございます。関係各位の皆様におかれましては、本日はどう...   
6                                                None   
7   山川委員　立憲民主党・市民クラブの山川百合子でございます。初めての国会での、外務委員会での質...   
8                                           

### Export data as a csv file
- Note: The file size is about 430KB. 

In [25]:
data.to_csv("syuuin_speech_tpp2017.csv",encoding="UTF-8")